####We will load data from bronze to silver here for one of the source systems and encourage the trainees to load the data for the other source system.<br> 
######Here we will do basic transformations like, column selection, filtering, deduplication, schema enforment, etc.

In [0]:
#create schema for silver if it does not exist
spark.sql("""CREATE SCHEMA IF NOT EXISTS psl_salesdev.silver MANAGED LOCATION 'abfss://sales@stavikaslakefreetrail.dfs.core.windows.net/silver/'""")

DataFrame[]

####First we will read our order bronze table directly from the source using catalog reference

In [0]:
df_orderdetails_retail=spark.table("psl_salesdev.bronze.ordersdetails_retail")
# Product ID:string
# Category:string
# Sub-Category:string
# Product Name:string

#Product table - Silver data load

Column pruning- We will only select the required columns from the orders table

In [0]:
df_selected=df_orderdetails_retail.select("Product ID","Product Name","Sub-Category","Category","Source")

In [0]:
df_selected.limit(5).display()

Product ID Product Name Sub-Category Category Source FUR-BO-10001798 Bush Somerset Collection Bookcase Bookcases Furniture Retail CSV FUR-CH-10000454 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back Chairs Furniture Retail CSV OFF-LA-10000240 Self-Adhesive Address Labels for Typewriters by Universal Labels Office Supplies Retail CSV FUR-TA-10000577 Bretford CR4500 Series Slim Rectangular Table Tables Furniture Retail CSV OFF-ST-10000760 Eldon Fold 'N Roll Cart System Storage Office Supplies Retail CSV

####Standardise Column Names

In [0]:
df_selected_std=df_selected.withColumnRenamed("Product ID","productID").withColumnRenamed("Product Name","productName").withColumnRenamed("Sub-Category","subCategory").withColumnRenamed("Category","category").withColumnRenamed("Source","source")

Remove Duplicates from the source

In [0]:
#drop duplicates from the selected dataframe
df_deduplicated=df_selected_std.dropDuplicates()

In [0]:
df_deduplicated.display()

productID productName subCategory category source TEC-PH-10000486 Plantronics HL10 Handset Lifter Phones Technology Retail CSV TEC-AC-10003832 Logitech P710e Mobile Speakerphone Accessories Technology Retail CSV TEC-AC-10002076 Microsoft Natural Keyboard Elite Accessories Technology Retail CSV TEC-PH-10004667 Cisco 8x8 Inc. 6753i IP Business Phone System Phones Technology Retail CSV OFF-BI-10000545 GBC Ibimaster 500 Manual ProClick Binding System Binders Office Supplies Retail CSV OFF-PA-10003543 Xerox 1985 Paper Office Supplies Retail CSV OFF-PA-10000994 Xerox 1915 Paper Office Supplies Retail CSV FUR-TA-10003008 Lesro Round Back Collection Coffee Table, End Table Tables Furniture Retail CSV OFF-PA-10002464 HP Office Recycled Paper (20Lb. and 87 Bright) Paper Office Supplies Retail CSV TEC-AC-10001109 Logitech Trackman Marble Mouse Accessories Technology Retail CSV FUR-FU-10004904 "Eldon ""L"" Workstation Diamond Chairmat" Furnishings Furniture Retail CSV OFF-PA-10000246 Riverleaf Stik-Withit Designer Note Cubes Paper Office Supplies Retail CSV OFF-LA-10003388 Avery 5 Labels Office Supplies Retail CSV TEC-MA-10003673 Hewlett-Packard Desktjet 6988DT Refurbished Printer Machines Technology Retail CSV OFF-BI-10001890 Avery Poly Binder Pockets Binders Office Supplies Retail CSV OFF-BI-10000136 Avery Non-Stick Heavy Duty View Round Locking Ring Binders Binders Office Supplies Retail CSV TEC-AC-10002018 AmazonBasics 3-Button USB Wired Mouse Accessories Technology Retail CSV TEC-MA-10000423 Texas Instruments TI-34 Scientific Calculator Machines Technology Retail CSV OFF-SU-10004290 "Acme Design Line 8"" Stainless Steel Bent Scissors w/Champagne Handles Supplies Office Supplies Retail CSV OFF-PA-10002479 Xerox 4200 Series MultiUse Premium Copy Paper (20Lb. and 84 Bright) Paper Office Supplies Retail CSV OFF-ST-10004180 Safco Commercial Shelving Storage Office Supplies Retail CSV FUR-FU-10001861 Floodlight Indoor Halogen Bulbs, 1 Bulb per Pack, 60 Watts Furnishings Furniture Retail CSV FUR-TA-10002041 Bevis Round Conference Table Top, X-Base Tables Furniture Retail CSV OFF-AR-10004974 Newell 342 Art Office Supplies Retail CSV OFF-BI-10001294 Fellowes Binding Cases Binders Office Supplies Retail CSV OFF-PA-10003656 Xerox 1935 Paper Office Supplies Retail CSV TEC-CO-10004202 Brother DCP1000 Digital 3 in 1 Multifunction Machine Copiers Technology Retail CSV OFF-ST-10000464 Multi-Use Personal File Cart and Caster Set, Three Stacking Bins Storage Office Supplies Retail CSV OFF-PA-10001295 Computer Printout Paper with Letter-Trim Perforations Paper Office Supplies Retail CSV TEC-PH-10003072 Panasonic KX-TG9541B DECT 6.0 Digital 2-Line Expandable Cordless Phone With Digital Answering System Phones Technology Retail CSV FUR-TA-10002607 KI Conference Tables Tables Furniture Retail CSV FUR-FU-10000023 Eldon Wave Desk Accessories Furnishings Furniture Retail CSV TEC-AC-10001101 Sony 16GB Class 10 Micro SDHC R40 Memory Card Accessories Technology Retail CSV OFF-ST-10000025 Fellowes Stor/Drawer Steel Plus Storage Drawers Storage Office Supplies Retail CSV TEC-PH-10002200 Samsung Galaxy Note 2 Phones Technology Retail CSV OFF-PA-10000675 Xerox 1919 Paper Office Supplies Retail CSV TEC-AC-10002800 Plantronics Audio 478 Stereo USB Headset Accessories Technology Retail CSV OFF-BI-10003963 Cardinal Holdit Data Disk Pockets Binders Office Supplies Retail CSV OFF-PA-10003022 Xerox 1992 Paper Office Supplies Retail CSV TEC-PH-10000213 Seidio BD2-HK3IPH5-BK DILEX Case and Holster Combo for Apple iPhone 5/5s - Black Phones Technology Retail CSV FUR-FU-10001379 "Executive Impressions 16-1/2"" Circular Wall Clock" Furnishings Furniture Retail CSV TEC-PH-10003273 AT&T TR1909W Phones Technology Retail CSV OFF-PA-10003465 Xerox 1912 Paper Office Supplies Retail CSV FUR-CH-10001482 Office Star - Mesh Screen back chair with Vinyl seat Chairs Furniture Retail CSV OFF-BI-10001097 Avery Hole Reinforcements Binders Office Supplies Retail CSV TEC-CO-10001046 Canon Imag

Add current timestamp

In [0]:
from pyspark.sql.functions import current_timestamp

df_cleaned=df_deduplicated.withColumn("ingestionTimestamp", current_timestamp())

In [0]:
df_cleaned.limit(5).display()

productID productName subCategory category source ingestionTimestamp TEC-PH-10000486 Plantronics HL10 Handset Lifter Phones Technology Retail CSV 2024-09-09T19:20:21.623Z TEC-AC-10003832 Logitech P710e Mobile Speakerphone Accessories Technology Retail CSV 2024-09-09T19:20:21.623Z TEC-AC-10002076 Microsoft Natural Keyboard Elite Accessories Technology Retail CSV 2024-09-09T19:20:21.623Z TEC-PH-10004667 Cisco 8x8 Inc. 6753i IP Business Phone System Phones Technology Retail CSV 2024-09-09T19:20:21.623Z OFF-BI-10000545 GBC Ibimaster 500 Manual ProClick Binding System Binders Office Supplies Retail CSV 2024-09-09T19:20:21.623Z

while creating tables with create table statement in databricks, databricks by default creates delta tables

In [0]:
spark.sql("""
CREATE TABLE IF NOT EXISTS psl_salesdev.silver.product_cleaned
(
  productID STRING NOT NULL COMMENT 'Unique identifier for each product',
  productName STRING NOT NULL COMMENT 'Name of the product',
  subCategory STRING COMMENT 'Sub-category of the product',
  category STRING COMMENT 'Category of the product',
  source STRING COMMENT 'Source system of the data',
  ingestionTimestamp TIMESTAMP COMMENT 'Timestamp when the data was ingested'
)
COMMENT 'This external table contains cleaned product data, partitioned by ingestion timestamp'
PARTITIONED BY (ingestionTimestamp)
LOCATION 'abfss://sales@stavikaslakefreetrail.dfs.core.windows.net/silver/product_cleaned'
""")


DataFrame[]

The mergeScehma command below will help in the schema evolution as and when needed

In [0]:
df_cleaned.write.mode("overwrite").option("mergeSchema", True).partitionBy("ingestionTimestamp").saveAsTable("psl_salesdev.silver.product_cleaned")

Let us now, verify if our data write was succesful

In [0]:
spark.table("psl_salesdev.silver.product_cleaned").display()

productID productName subCategory category source ingestionTimestamp TEC-PH-10000486 Plantronics HL10 Handset Lifter Phones Technology Retail CSV 2024-09-09T19:36:52.229Z TEC-AC-10003832 Logitech P710e Mobile Speakerphone Accessories Technology Retail CSV 2024-09-09T19:36:52.229Z TEC-AC-10002076 Microsoft Natural Keyboard Elite Accessories Technology Retail CSV 2024-09-09T19:36:52.229Z TEC-PH-10004667 Cisco 8x8 Inc. 6753i IP Business Phone System Phones Technology Retail CSV 2024-09-09T19:36:52.229Z OFF-BI-10000545 GBC Ibimaster 500 Manual ProClick Binding System Binders Office Supplies Retail CSV 2024-09-09T19:36:52.229Z OFF-PA-10003543 Xerox 1985 Paper Office Supplies Retail CSV 2024-09-09T19:36:52.229Z OFF-PA-10000994 Xerox 1915 Paper Office Supplies Retail CSV 2024-09-09T19:36:52.229Z FUR-TA-10003008 Lesro Round Back Collection Coffee Table, End Table Tables Furniture Retail CSV 2024-09-09T19:36:52.229Z OFF-PA-10002464 HP Office Recycled Paper (20Lb. and 87 Bright) Paper Office Supplies Retail CSV 2024-09-09T19:36:52.229Z TEC-AC-10001109 Logitech Trackman Marble Mouse Accessories Technology Retail CSV 2024-09-09T19:36:52.229Z FUR-FU-10004904 "Eldon ""L"" Workstation Diamond Chairmat" Furnishings Furniture Retail CSV 2024-09-09T19:36:52.229Z OFF-PA-10000246 Riverleaf Stik-Withit Designer Note Cubes Paper Office Supplies Retail CSV 2024-09-09T19:36:52.229Z OFF-LA-10003388 Avery 5 Labels Office Supplies Retail CSV 2024-09-09T19:36:52.229Z TEC-MA-10003673 Hewlett-Packard Desktjet 6988DT Refurbished Printer Machines Technology Retail CSV 2024-09-09T19:36:52.229Z OFF-BI-10001890 Avery Poly Binder Pockets Binders Office Supplies Retail CSV 2024-09-09T19:36:52.229Z OFF-BI-10000136 Avery Non-Stick Heavy Duty View Round Locking Ring Binders Binders Office Supplies Retail CSV 2024-09-09T19:36:52.229Z TEC-AC-10002018 AmazonBasics 3-Button USB Wired Mouse Accessories Technology Retail CSV 2024-09-09T19:36:52.229Z TEC-MA-10000423 Texas Instruments TI-34 Scientific Calculator Machines Technology Retail CSV 2024-09-09T19:36:52.229Z OFF-SU-10004290 "Acme Design Line 8"" Stainless Steel Bent Scissors w/Champagne Handles Supplies Office Supplies Retail CSV 2024-09-09T19:36:52.229Z OFF-PA-10002479 Xerox 4200 Series MultiUse Premium Copy Paper (20Lb. and 84 Bright) Paper Office Supplies Retail CSV 2024-09-09T19:36:52.229Z OFF-ST-10004180 Safco Commercial Shelving Storage Office Supplies Retail CSV 2024-09-09T19:36:52.229Z FUR-FU-10001861 Floodlight Indoor Halogen Bulbs, 1 Bulb per Pack, 60 Watts Furnishings Furniture Retail CSV 2024-09-09T19:36:52.229Z FUR-TA-10002041 Bevis Round Conference Table Top, X-Base Tables Furniture Retail CSV 2024-09-09T19:36:52.229Z OFF-AR-10004974 Newell 342 Art Office Supplies Retail CSV 2024-09-09T19:36:52.229Z OFF-BI-10001294 Fellowes Binding Cases Binders Office Supplies Retail CSV 2024-09-09T19:36:52.229Z OFF-PA-10003656 Xerox 1935 Paper Office Supplies Retail CSV 2024-09-09T19:36:52.229Z TEC-CO-10004202 Brother DCP1000 Digital 3 in 1 Multifunction Machine Copiers Technology Retail CSV 2024-09-09T19:36:52.229Z OFF-ST-10000464 Multi-Use Personal File Cart and Caster Set, Three Stacking Bins Storage Office Supplies Retail CSV 2024-09-09T19:36:52.229Z OFF-PA-10001295 Computer Printout Paper with Letter-Trim Perforations Paper Office Supplies Retail CSV 2024-09-09T19:36:52.229Z TEC-PH-10003072 Panasonic KX-TG9541B DECT 6.0 Digital 2-Line Expandable Cordless Phone With Digital Answering System Phones Technology Retail CSV 2024-09-09T19:36:52.229Z FUR-TA-10002607 KI Conference Tables Tables Furniture Retail CSV 2024-09-09T19:36:52.229Z FUR-FU-10000023 Eldon Wave Desk Accessories Furnishings Furniture Retail CSV 2024-09-09T19:36:52.229Z TEC-AC-10001101 Sony 16GB Class 10 Micro SDHC R40 Memory Card Accessories Technology Retail CSV 2024-09-09T19:36:52.229Z OFF-ST-10000025 Fellowes Stor/Drawer Steel Plus Storage Drawers Storage Office Supplies Retail CSV 2024-09-09T19:36:52.229Z TEC-PH-10002200 Samsung Galaxy Note 2 Ph

------------------------------------------------------------------------------

#Sales table

column Pruning- We will only select the columns required for the sales caculation

In [0]:
df_sales_selected=df_orderdetails_retail.select("Order ID","Order Date","Product ID","Sales","Quantity","Profit","Source")


We now want to standardise the column names using Functions

In [0]:
# Function to convert a single column name to camelCase
def to_camel_case(column_name):
    words = column_name.split(" ")  # Split by space
    if len(words) == 1:  # If it's a single word or character, return it in lowercase
        return words[0].lower()
    else:
        return words[0].lower() + "".join(word.capitalize() for word in words[1:])

# Function to standardize column names using withColumnRenamed and a loop
def standardize_columns(df):
    for old_col in df.columns:
        new_col = to_camel_case(old_col)  # Apply the camelCase transformation
        df = df.withColumnRenamed(old_col, new_col)  # Rename each column
    return df

#Function to add an ingestion timestamp
from pyspark.sql.functions import current_timestamp, col, to_date
def add_ingestionTimesatmp(df):
    return df.withColumn("ingestionTimestamp", current_timestamp())

In [0]:
#standardize columns
df_sales_standarized=standardize_columns(df_sales_selected)

#add ingestion timestamp
df_sales_standarized=add_ingestionTimesatmp(df_sales_standarized)

#convert orderDate into Date format
df_sales_standarized=df_sales_standarized.withColumn("orderDate", to_date(col("orderDate"), "dd/MM/yy"))

%md
##to_date 
function in PySpark is used to convert a string column containing date-like values into a proper DateType column. This function allows you to specify the format of the input date string, so it can interpret and parse the date correctly.

Key Features:
Input: The function takes a string column and a date format as input.
Format: You need to provide a date format (e.g., "MM/dd/yyyy", "dd-MM-yyyy") to let the function know how to interpret the string.
Output: It converts the string into a DateType, which is useful for performing date-related operations like filtering, comparisons, or date arithmetic

<br>
<b>Let us take a look at the modified dataframe

In [0]:
df_sales_standarized.display()

orderId orderDate productId sales quantity profit source ingestionTimestamp CA-2016-152156 2016-11-08 FUR-BO-10001798 261.96 2.0 41.9136 Retail CSV 2024-09-10T07:30:24.932Z CA-2016-152156 2016-11-08 FUR-CH-10000454 731.94 3.0 219.582 Retail CSV 2024-09-10T07:30:24.932Z CA-2016-138688 2016-06-12 OFF-LA-10000240 14.62 2.0 6.8714 Retail CSV 2024-09-10T07:30:24.932Z US-2015-108966 2015-10-11 FUR-TA-10000577 957.5775 5.0 -383.031 Retail CSV 2024-09-10T07:30:24.932Z US-2015-108966 2015-10-11 OFF-ST-10000760 22.368 2.0 2.5164 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-115812 2014-06-09 FUR-FU-10001487 48.86 7.0 14.1694 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-115812 2014-06-09 OFF-AR-10002833 7.28 4.0 1.9656 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-115812 2014-06-09 TEC-PH-10002275 907.152 6.0 90.7152 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-115812 2014-06-09 OFF-BI-10003910 18.504 3.0 5.7825 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-115812 2014-06-09 OFF-AP-10002892 114.9 5.0 34.47 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-115812 2014-06-09 FUR-TA-10001539 1706.184 9.0 85.3092 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-115812 2014-06-09 TEC-PH-10002033 911.424 4.0 68.3568 Retail CSV 2024-09-10T07:30:24.932Z CA-2017-114412 2017-04-15 OFF-PA-10002365 15.552 3.0 5.4432 Retail CSV 2024-09-10T07:30:24.932Z CA-2016-161389 2016-12-05 OFF-BI-10003656 407.976 3.0 132.5922 Retail CSV 2024-09-10T07:30:24.932Z US-2015-118983 2015-11-22 OFF-AP-10002311 68.81 5.0 -123.858 Retail CSV 2024-09-10T07:30:24.932Z US-2015-118983 2015-11-22 OFF-BI-10000756 2.544 3.0 -3.816 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-105893 2014-11-11 OFF-ST-10004186 665.88 6.0 13.3176 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-167164 2014-05-13 OFF-ST-10000107 55.5 2.0 9.99 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-143336 2014-08-27 OFF-AR-10003056 8.56 2.0 2.4824 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-143336 2014-08-27 TEC-PH-10001949 213.48 3.0 16.011 Retail CSV 2024-09-10T07:30:24.932Z CA-2014-143336 2014-08-27 OFF-BI-10002215 22.72 4.0 7.384 Retail CSV 2024-09-10T07:30:24.932Z CA-2016-137330 2016-12-09 OFF-AR-10000246 19.46 7.0 5.0596 Retail CSV 2024-09-10T07:30:24.932Z CA-2016-137330 2016-12-09 OFF-AP-10001492 60.34 7.0 15.6884 Retail CSV 2024-09-10T07:30:24.932Z US-2017-156909 2017-07-16 FUR-CH-10002774 71.372 2.0 -1.0196 Retail CSV 2024-09-10T07:30:24.932Z CA-2015-106320 2015-09-25 FUR-TA-10000577 1044.63 3.0 240.2649 Retail CSV 2024-09-10T07:30:24.932Z CA-2016-121755 2016-01-16 OFF-BI-10001634 11.648 2.0 4.2224 Retail CSV 2024-09-10T07:30:24.932Z CA-2016-121755 2016-01-16 TEC-AC-10003027 90.57 3.0 11.7741 Retail CSV 2024-09-10T07:30:24.932Z US-2015-150630 2015-09-17 FUR-BO-10004834 3083.43 7.0 -1665.0522 Retail CSV 2024-09-10T07:30:24.932Z US-2015-150630 2015-09-17 OFF-BI-10000474 9.618 2.0 -7.0532 Retail CSV 2024-09-10T07:30:24.932Z US-2015-150630 2015-09-17 FUR-FU-10004848 124.2 3.0 15.525 Retail CSV 2024-09-10T07:30:24.932Z US-2015-150630 2015-09-17 OFF-EN-10001509 3.264 2.0 1.1016 Retail CSV 2024-09-10T07:30:24.932Z US-2015-150630 2015-09-17 OFF-AR-10004042 86.304 6.0 9.7092 Retail CSV 2024-09-10T07:30:24.932Z US-2015-150630 2015-09-17 OFF-BI-10001525 null 6.858 0.7 Retail CSV 2024-09-10T07:30:24.932Z US-2015-150630 2015-09-17 OFF-AR-10001683 15.76 2.0 3.546 Retail CSV 2024-09-10T07:30:24.932Z CA-2017-107727 2017-10-19 OFF-PA-10000249 29.472 3.0 9.9468 Retail CSV 2024-09-10T07:30:24.932Z CA-2016-117590 2016-12-08 TEC-PH-10004977 1097.544 7.0 123.4737 Retail CSV 2024-09-10T07:30:24.932Z CA-2016-117590 2016-12-08 FUR-FU-10003664 190.92 5.0 -147.963 Retail CSV 2024-09-10T07:30:24.932Z CA-2015-117415 2015-12-27 OFF-EN-10002986 113.328 9.0 35.415 Retail CSV 2024-09-10T07:30:24.932Z CA-2015-117415 2015-12-27 FUR-BO-10002545 532.3992 3.0 -46.9764 Retail CSV 2024-09-10T07:30:24.932Z CA-2015-117415 2015-12-27 FUR-CH-10004218 212.058 3.0 -15.147 Retail CSV 2024-09-10T07:30:24.932Z CA-2015-117415 2015-12-27 TEC-PH-10000486 371.168 4.0 41.7564 Reta

Now we will create an external table for our silver table for sales

In [0]:
spark.sql("""
CREATE TABLE if not exists psl_salesdev.silver.sales_cleaned (
    orderId STRING COMMENT 'Unique identifier for each order',
    orderDate DATE COMMENT 'Date of the order',
    productId STRING COMMENT 'Unique identifier for each product',
    sales DOUBLE COMMENT 'Sales amount for the order',
    quantity DOUBLE COMMENT 'Quantity of products sold',
    profit DOUBLE COMMENT 'Profit made from the sale',
    source STRING COMMENT 'Source of the order (e.g., online, in-store)',
    ingestionTimestamp TIMESTAMP COMMENT 'Timestamp of data ingestion'
)
COMMENT 'This table stores sales order details'
PARTITIONED BY (ingestionTimestamp)
LOCATION 'abfss://sales@stavikaslakefreetrail.dfs.core.windows.net/silver/sales_cleaned/'
""")

DataFrame[]

write sales data to the silver layer

In [0]:
df_sales_standarized.write.mode("overwrite").saveAsTable("psl_salesdev.silver.sales_cleaned")

In [0]:
%sql
select * from psl_salesdev.silver.sales_cleaned

orderId orderDate productId sales quantity profit source ingestionTimestamp CA-2016-152156 2016-11-08 FUR-BO-10001798 261.96 2.0 41.9136 Retail CSV 2024-09-10T07:40:05.637Z CA-2016-152156 2016-11-08 FUR-CH-10000454 731.94 3.0 219.582 Retail CSV 2024-09-10T07:40:05.637Z CA-2016-138688 2016-06-12 OFF-LA-10000240 14.62 2.0 6.8714 Retail CSV 2024-09-10T07:40:05.637Z US-2015-108966 2015-10-11 FUR-TA-10000577 957.5775 5.0 -383.031 Retail CSV 2024-09-10T07:40:05.637Z US-2015-108966 2015-10-11 OFF-ST-10000760 22.368 2.0 2.5164 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-115812 2014-06-09 FUR-FU-10001487 48.86 7.0 14.1694 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-115812 2014-06-09 OFF-AR-10002833 7.28 4.0 1.9656 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-115812 2014-06-09 TEC-PH-10002275 907.152 6.0 90.7152 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-115812 2014-06-09 OFF-BI-10003910 18.504 3.0 5.7825 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-115812 2014-06-09 OFF-AP-10002892 114.9 5.0 34.47 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-115812 2014-06-09 FUR-TA-10001539 1706.184 9.0 85.3092 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-115812 2014-06-09 TEC-PH-10002033 911.424 4.0 68.3568 Retail CSV 2024-09-10T07:40:05.637Z CA-2017-114412 2017-04-15 OFF-PA-10002365 15.552 3.0 5.4432 Retail CSV 2024-09-10T07:40:05.637Z CA-2016-161389 2016-12-05 OFF-BI-10003656 407.976 3.0 132.5922 Retail CSV 2024-09-10T07:40:05.637Z US-2015-118983 2015-11-22 OFF-AP-10002311 68.81 5.0 -123.858 Retail CSV 2024-09-10T07:40:05.637Z US-2015-118983 2015-11-22 OFF-BI-10000756 2.544 3.0 -3.816 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-105893 2014-11-11 OFF-ST-10004186 665.88 6.0 13.3176 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-167164 2014-05-13 OFF-ST-10000107 55.5 2.0 9.99 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-143336 2014-08-27 OFF-AR-10003056 8.56 2.0 2.4824 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-143336 2014-08-27 TEC-PH-10001949 213.48 3.0 16.011 Retail CSV 2024-09-10T07:40:05.637Z CA-2014-143336 2014-08-27 OFF-BI-10002215 22.72 4.0 7.384 Retail CSV 2024-09-10T07:40:05.637Z CA-2016-137330 2016-12-09 OFF-AR-10000246 19.46 7.0 5.0596 Retail CSV 2024-09-10T07:40:05.637Z CA-2016-137330 2016-12-09 OFF-AP-10001492 60.34 7.0 15.6884 Retail CSV 2024-09-10T07:40:05.637Z US-2017-156909 2017-07-16 FUR-CH-10002774 71.372 2.0 -1.0196 Retail CSV 2024-09-10T07:40:05.637Z CA-2015-106320 2015-09-25 FUR-TA-10000577 1044.63 3.0 240.2649 Retail CSV 2024-09-10T07:40:05.637Z CA-2016-121755 2016-01-16 OFF-BI-10001634 11.648 2.0 4.2224 Retail CSV 2024-09-10T07:40:05.637Z CA-2016-121755 2016-01-16 TEC-AC-10003027 90.57 3.0 11.7741 Retail CSV 2024-09-10T07:40:05.637Z US-2015-150630 2015-09-17 FUR-BO-10004834 3083.43 7.0 -1665.0522 Retail CSV 2024-09-10T07:40:05.637Z US-2015-150630 2015-09-17 OFF-BI-10000474 9.618 2.0 -7.0532 Retail CSV 2024-09-10T07:40:05.637Z US-2015-150630 2015-09-17 FUR-FU-10004848 124.2 3.0 15.525 Retail CSV 2024-09-10T07:40:05.637Z US-2015-150630 2015-09-17 OFF-EN-10001509 3.264 2.0 1.1016 Retail CSV 2024-09-10T07:40:05.637Z US-2015-150630 2015-09-17 OFF-AR-10004042 86.304 6.0 9.7092 Retail CSV 2024-09-10T07:40:05.637Z US-2015-150630 2015-09-17 OFF-BI-10001525 null 6.858 0.7 Retail CSV 2024-09-10T07:40:05.637Z US-2015-150630 2015-09-17 OFF-AR-10001683 15.76 2.0 3.546 Retail CSV 2024-09-10T07:40:05.637Z CA-2017-107727 2017-10-19 OFF-PA-10000249 29.472 3.0 9.9468 Retail CSV 2024-09-10T07:40:05.637Z CA-2016-117590 2016-12-08 TEC-PH-10004977 1097.544 7.0 123.4737 Retail CSV 2024-09-10T07:40:05.637Z CA-2016-117590 2016-12-08 FUR-FU-10003664 190.92 5.0 -147.963 Retail CSV 2024-09-10T07:40:05.637Z CA-2015-117415 2015-12-27 OFF-EN-10002986 113.328 9.0 35.415 Retail CSV 2024-09-10T07:40:05.637Z CA-2015-117415 2015-12-27 FUR-BO-10002545 532.3992 3.0 -46.9764 Retail CSV 2024-09-10T07:40:05.637Z CA-2015-117415 2015-12-27 FUR-CH-10004218 212.058 3.0 -15.147 Retail CSV 2024-09-10T07:40:05.637Z CA-2015-117415 2015-12-27 TEC-PH-10000486 371.168 4.0 41.7564 Reta